In [1]:
import agentpy as ap
import numpy as np
import matplotlib.pyplot as plt
import math
import IPython
import json

In [2]:
class Semaphore(ap.Agent):
    def setup(self):
        self.step_time = 0.1
        self.direction = [0, 1]
        self.state = 0 #verde = 0, amarillo = 1, rojo = 2
        self.state_time = 0

        self.green_duration = 50
        self.yellow_duration = 5
        self.red_duration = 45

    def update(self) :
        self.state_time += self.step_time


        if self.state == 0:
            if self.state_time >= self.green_duration:
                self.state = 1
                self.state_time = 0

        if self.state == 1:
            if self.state_time >= self.yellow_duration:
                self.state = 2
                self.state_time = 0

        if self.state == 2:
            if self.state_time >= self.red_duration:
                self.state = 0
                self.state_time = 0

    def set_green(self):
        self.state = 0
        self.state_time = 0
    
    def set_yellow(self):
        self.state = 1
        self.state_time = 0

    def set_red(self):
        self.state = 2
        self.state_time = 0

In [3]:
class Car(ap.Agent):
    def setup(self):
        self.step_time = 0.1
        self.direction = [0, 1]
        self.dir = 9
        self.id = "placeholder"
        self.speed = 0.0
        self.max_speed = 16.66
        self.state = 1 # 0 = chocado, 1 = ok

    def update_position(self):
        if self.state == 0:
            return
        
        self.model.avenue.move_by(self, [self.speed*self.step_time*self.direction[0], self.speed*self.step_time*self.direction[1]])

    def update_speed(self):
        if self.state == 0:
            return
        
        p = self.model.avenue.positions[self]

        min_car_distance = 10000000
        for car in self.model.cars:
            if car == self:
                continue

            dot_p1 = self.direction[0]*car.direction[0] + self.direction[1]*car.direction[1]

            p2 = self.model.avenue.positions[car]
            dot_p2 = (p2[0] - p[0])*self.direction[0] + (p2[1] - p[1])*self.direction[1]

            if dot_p1 > 0 and dot_p2 > 0:
                d = math.sqrt((p2[0] - p[0])**2 + (p2[1] - p[1])**2)
                if d < min_car_distance:
                    min_car_distance = d

        min_semaphore_distance = 10000000
        semaphore_state = 0
        for semaphore in self.model.semaphores:

            dot_p1 = self.direction[0]*semaphore.direction[0] + self.direction[1]*semaphore.direction[1]

            p2 = self.model.avenue.positions[semaphore]
            dot_p2 = (p2[0] - p[0])*self.direction[0] + (p2[1] - p[1])*self.direction[1]

            if dot_p1 < 0 and dot_p2 > 0:
                d = math.sqrt((p2[0] - p[0])**2 + (p2[1] - p[1])**2)
                if d < min_semaphore_distance:
                    min_semaphore_distance = d
                    semaphore_state = semaphore.state
                
        if min_car_distance < 10:
            self.speed = 0
            self.state = 1

        elif min_car_distance < 10:
            self.speed = np.maximum(self.speed - 10*self.step_time, 0)
        
        elif min_car_distance < 15:
            self.speed = np.maximum(self.speed - 5*self.step_time, 0)

        elif min_semaphore_distance < 55 and semaphore_state == 1:
            self.speed = np.maximum(self.speed + 10.5*self.step_time, self.max_speed)

        elif min_semaphore_distance < 50 and semaphore_state == 0:
            self.speed = np.maximum(self.speed + 4*self.step_time, 5)

        elif min_semaphore_distance < 70 and semaphore_state == 1:
            self.speed = np.maximum(self.speed - 7*self.step_time, 5)

        elif min_semaphore_distance < 47.5 and semaphore_state == 2:
            self.speed = np.maximum(self.speed - 10*self.step_time, 0)

        elif min_semaphore_distance < 50 and semaphore_state == 2:
            self.speed = np.maximum(self.speed - 2.5*self.step_time, 5)

        else:
            self.speed = np.minimum(self.speed + 2.0*self.step_time, self.max_speed)


In [4]:
class AvenueModel(ap.Model):
    def setup(self):
        self.cars = ap.AgentList(self, self.p.cars, Car)
        self.cars.step_time = self.p.step_time
        self.cars.speed = self.p.v0

        c_north = int(self.p.cars/2)
        c_south = self.p.cars - (c_north)



        for k in range(c_north):
            self.cars[k].direction = [0, 1]

        for k in range(c_south):
            self.cars[c_north + k].direction = [0, -1]
        
        
        
        self.semaphores = ap.AgentList(self, 4, Semaphore)
        self.semaphores.step_time = self.p.step_time
        self.semaphores.green_duration = self.p.green
        self.semaphores.yellow_duration = self.p.yellow
        self.semaphores.red_duration = self.p.red
        self.semaphores[0].direction = [0, 1]
        self.semaphores[1].direction = [0, -1]
        self.semaphores[2].direction = [-1, 0]
        self.semaphores[3].direction = [1, 0]

        self.avenue = ap.Space(self, shape = [60, self.p.size], torus = True)

        self.avenue.add_agents(self.semaphores, random=True)
        self.avenue.move_to(self.semaphores[0], [0, self.p.size*0.5 - 15])
        self.avenue.move_to(self.semaphores[1], [55, self.p.size*0.5 + 15])
        self.avenue.move_to(self.semaphores[2], [0, self.p.size*0.5 + 15])
        self.avenue.move_to(self.semaphores[3], [55, self.p.size*0.5 - 15])

        self.avenue.add_agents(self.cars, random=True)

        for k in range(c_north):
            self.avenue.move_to(self.cars[k], [30, 10*(k+1)])
            self.cars[k].dir = 1
            self.cars[k].id = "car"+str(k)

        for k in range(c_south):
            self.avenue.move_to(self.cars[k+c_north], [25, self.p.size - 10*(k+1)])
            self.cars[k+c_north].dir = 0
            self.cars[k+c_north].id = "car"+str(k+c_north)

    def step(self):
        self.semaphores.update()

        self.cars.update_position()
        self.cars.update_speed()
    
    def update(self):
        crashes = len(self.cars.select(self.cars.state == 0))
        self.record('Colisiones', crashes)
    
    def end(self):
        crashes = len(self.cars.select(self.cars.state == 0))
        self.report('Colisiones', crashes)


In [5]:
parameters = {
    'steps' : 350,
    'step_time' : 0.2,
    'size' : 300,
    'green' : 20,
    'yellow' : 8,
    'red' : 10,
    'cars' : 32,
    'v0' : 0,
}

# Visualización

In [6]:
jsonSimulation=[]
def animation_plot_single(m, ax):
    """ Esta función genera una gráfica que representa el estado del modelo indicado. """ 

    ax.set_title(f"Avenida t={m.t*m.p.step_time:.2f}")

    colors = ["green", "yellow", "red"]

    pos_s1 = m.avenue.positions[m.semaphores[0]]
    ax.scatter(*pos_s1, s=20, c=colors[m.semaphores[0].state])

    pos_s2 = m.avenue.positions[m.semaphores[1]]
    ax.scatter(*pos_s2, s=20, c=colors[m.semaphores[1].state])

    pos_s3 = m.avenue.positions[m.semaphores[2]]
    ax.scatter(*pos_s3, s=20, c=colors[m.semaphores[2].state])

    pos_s4 = m.avenue.positions[m.semaphores[3]]
    ax.scatter(*pos_s4, s=20, c=colors[m.semaphores[3].state])

    ax.set_xlim(-10, m.avenue.shape[0])
    ax.set_ylim(-10, m.avenue.shape[1])

    step=[]
    for car in m.cars:

        pos_c = m.avenue.positions[car]
        ax.scatter(*pos_c, s=20, c="black")

        carros = {
            "id": car.id,
            "x": math.ceil(pos_c[0]),
            "z": math.ceil(pos_c[1]),
            "dir": car.dir
        }
        step.append(carros)

    semaforos = {
        "color" : m.semaphores[0].state
    }
    #print(crr)
    finalJ={
    "carros": step,
    "semaforos":semaforos
    }

    jsonSimulation.append(finalJ)
        
    ax.set_axis_off()
    ax.set_aspect('equal', 'box')

def createJson(name, obj):
    with open(name, 'w') as file:
        json_string = json.dumps(obj, default=lambda o: o.__dict__, sort_keys=False, indent=4)
        file.write(json_string)

def animation_plot(m, p):
    """ Esta función auxiliar sirve para generar una animación para el modelo indicado llamando repetidamente la función animation_plot_single. """ 
    fig = plt.figure(figsize=(10, 10))
    ax = fig.add_subplot(111)
    animation = ap.animate(m(p), fig, ax, animation_plot_single)
    return IPython.display.HTML(animation.to_jshtml(fps=20))

In [7]:
model = AvenueModel(parameters)
results = model.run()

Completed: 350 steps
Run time: 0:00:01.226711
Simulation finished


In [8]:
# Autos colisionados en cada iteración
#results.variables.AvenueModel

In [9]:
# Información al final de la simulación
results.reporters

seed  Colisiones
0  168675013302476504933769588927682280586           0

In [10]:
animation_plot(AvenueModel, parameters)

In [11]:
finalJson={
    "steps": jsonSimulation
}
createJson("positions.json", finalJson)